# Probe Architecture Comparison

This notebook compares 9 novel probe architectures for predicting model confidence.

**Architectures tested:**
1. Default MLP (baseline)
2. AttentionProbe - Self-attention over hidden state chunks
3. ResidualProbe - Deep MLP with skip connections
4. BottleneckProbe - Compression to low-rank representation
5. MultiHeadProbe - Multiple experts with learned aggregation
6. GatedProbe - GLU-style gating
7. SparseProbe - Top-k dimension selection
8. HeteroscedasticProbe - Per-example uncertainty
9. BilinearProbe - Explicit feature interactions
10. HierarchicalProbe - Multi-scale hierarchical processing (fine → mid → semantic → global)

**Setup:** Run on Google Colab with GPU (Runtime > Change runtime type > T4 GPU)

In [1]:
%cd /content #unicorn

/content


In [2]:
!rm -rf /content/deep-learning
!rm -rf deep-learning
!rm -rf deep-learning* #unicorn

In [3]:
# Install dependencies (Colab)
!pip install -q transformers accelerate bitsandbytes datasets tqdm matplotlib seaborn scikit-learn

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.4/59.4 MB 45.1 MB/s eta 0:00:00


In [4]:
# Clone repo and setup path
!git clone -b maureen --single-branch https://github.com/joshcliu/deep-learning.git #unicorn
%cd deep-learning

import sys
sys.path.insert(0, '.')

Cloning into 'deep-learning'...
remote: Enumerating objects: 355, done.
remote: Counting objects: 100% (34/34), done.
remote: Compressing objects: 100% (26/26), done.
remote: Total 355 (delta 19), reused 19 (delta 8), pack-reused 321 (from 1)
Receiving objects: 100% (355/355), 257.29 KiB | 9.90 MiB/s, done.
Resolving deltas: 100% (180/180), done.
/content/deep-learning


In [5]:
# Patch for bfloat16 compatibility (8-bit quantized models)
import numpy as np
import torch
from src.models import extractor as extractor_module

_original_extract_batch = extractor_module.HiddenStateExtractor._extract_batch

def _patched_extract_batch(self, texts, layers, max_length, token_position):
    """Patched to preserve original behavior while safely handling bfloat16."""

    # 1. Tokenization (unchanged)
    encodings = self.tokenizer(
        texts,
        padding=True,
        truncation=True,
        max_length=max_length,
        return_tensors="pt",
    )
    encodings = {k: v.to(self.device) for k, v in encodings.items()}

    # 2. Model forward pass
    with torch.no_grad():
        outputs = self.model(
            **encodings,
            output_hidden_states=True,
            return_dict=True,
        )

    hidden_states = outputs.hidden_states
    batch_hiddens = []

    # 3. Iterate entire batch for each requested layer
    for layer_idx in layers:

        # IMPORTANT: your model uses layer_idx + 1
        layer_hiddens = hidden_states[layer_idx + 1]  # (batch, seq_len, hidden)

        # === TOKEN SELECTION (MUST FOLLOW ORIGINAL LOGIC) ===
        if token_position == "last":
            attention_mask = encodings["attention_mask"]
            seq_lengths = attention_mask.sum(dim=1) - 1
            token_hiddens = layer_hiddens[
                torch.arange(layer_hiddens.size(0), device=self.device),
                seq_lengths
            ]

        elif token_position == "cls":
            token_hiddens = layer_hiddens[:, 0, :]

        elif token_position == "mean":
            attention_mask = encodings["attention_mask"].unsqueeze(-1)
            masked_hiddens = layer_hiddens * attention_mask
            token_hiddens = masked_hiddens.sum(dim=1) / attention_mask.sum(dim=1)

        else:
            raise ValueError(f"Unknown token_position: {token_position}")

        # === BF16 / INT8 SAFE CONVERSION ===
        token_hiddens = token_hiddens.detach().cpu().to(torch.float32).numpy()

        batch_hiddens.append(token_hiddens)

    # 4. Stack layers: (batch, num_layers, hidden_dim)
    return np.stack(batch_hiddens, axis=1)


# Apply patch
extractor_module.HiddenStateExtractor._extract_batch = _patched_extract_batch
print("Patched HiddenStateExtractor for bfloat16 & 8bit compatibility.")

Patched HiddenStateExtractor for bfloat16 & 8bit compatibility.


## 1. Load Model

In [7]:
from src.models import ModelLoader, HiddenStateExtractor

# Load Mistral 7B (ungated, no approval needed)
model_name = "Qwen/Qwen2.5-7B"
loader = ModelLoader(model_name)
model, tokenizer = loader.load(quantization="8bit", device_map="auto")

print(f"Loaded {model_name}")
print(f"Layers: {loader.config.num_layers}, Hidden dim: {loader.config.hidden_dim}")

tokenizer_config.json: 0.00B [00:00, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

config.json:   0%|          | 0.00/686 [00:00<?, ?B/s]

...

model-00002-of-00004.safetensors:   0%|          | 0.00/3.86G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/3.56G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/138 [00:00<?, ?B/s]

Loaded Qwen/Qwen2.5-7B
Layers: 28, Hidden dim: 3584


## 2. Load Dataset

In [8]:
from src.data import MMLUDataset

# Load MMLU validation set
dataset = MMLUDataset(split="validation")
print(f"Loaded {len(dataset)} examples")

# Sample for experiment
NUM_SAMPLES = 2000  # Increased for better AUROC (was 300)
examples = dataset.sample(NUM_SAMPLES, seed=42)
print(f"Using {len(examples)} examples")

`trust_remote_code` is not supported anymore.
Please check that the Hugging Face dataset 'cais/mmlu' isn't based on a loading script and remove `trust_remote_code`.
If the dataset is based on a loading script, please ask the dataset author to remove it and convert it to a standard format like Parquet.
ERROR:datasets.load:`trust_remote_code` is not supported anymore.
Please check that the Hugging Face dataset 'cais/mmlu' isn't based on a loading script and remove `trust_remote_code`.
If the dataset is based on a loading script, please ask the dataset author to remove it and convert it to a standard format like Parquet.


README.md: 0.00B [00:00, ?B/s]

dataset_infos.json: 0.00B [00:00, ?B/s]

abstract_algebra/test-00000-of-00001.par(…):   0%|          | 0.00/9.96k [00:00<?, ?B/s]

abstract_algebra/validation-00000-of-000(…):   0%|          | 0.00/3.73k [00:00<?, ?B/s]

...

virology/dev-00000-of-00001.parquet:   0%|          | 0.00/3.87k [00:00<?, ?B/s]

Generating test split:   0%|          | 0/166 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/18 [00:00<?, ? examples/s]

Generating dev split:   0%|          | 0/5 [00:00<?, ? examples/s]

Loaded 1531 examples
Using 1531 examples


## 3. Generate Answers & Check Correctness

In [ ]:
from tqdm import tqdm

def generate_answer(model, tokenizer, prompt, max_new_tokens=32):
    """Generate model's answer to a question."""
    inputs = tokenizer(prompt, return_tensors="pt").to(model.device)

    with torch.no_grad():
        outputs = model.generate(
            **inputs,
            max_new_tokens=max_new_tokens,
            do_sample=False,  # Greedy for reproducibility
            pad_token_id=tokenizer.eos_token_id,
        )

    generated = tokenizer.decode(outputs[0][inputs.input_ids.shape[1]:], skip_special_tokens=True)
    return generated.strip()

def check_correctness(generated: str, example) -> bool:
    """Check if generated answer matches correct answer."""
    correct_answer = example.choices[example.answer]
    correct_letter = chr(65 + example.answer)  # A, B, C, D

    generated_lower = generated.lower().strip()

    # Check for letter match
    if generated_lower.startswith(correct_letter.lower()):
        return True

    # Check for answer text match
    if correct_answer.lower() in generated_lower:
        return True

    return False

# Generate answers for all examples
print("Generating model answers...")
prompts = []
correctness = []

for example in tqdm(examples):
    prompt = example.format_prompt(style="multiple_choice")
    prompts.append(prompt)

    generated = generate_answer(model, tokenizer, prompt)
    is_correct = check_correctness(generated, example)
    correctness.append(int(is_correct))

correctness = np.array(correctness)
print(f"\nAccuracy: {correctness.mean():.1%} ({correctness.sum()}/{len(correctness)})")

Generating model answers...


  0%|          | 0/1531 [00:00<?, ?it/s]/usr/local/lib/python3.12/dist-packages/bitsandbytes/autograd/_functions.py:181: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")
 20%|█▉        | 301/1531 [18:55<59:19,  2.89s/it]  

## 4. Extract Hidden States

In [ ]:
# Extract from multiple layers (quartiles) for multi-scale representation
# This enables hierarchical and attention probes to leverage layer-wise information
num_layers = loader.config.num_layers
LAYERS = [
    num_layers // 4,      # Early layer (Q1)
    num_layers // 2,      # Middle layer (Q2)
    3 * num_layers // 4,  # Late layer (Q3)
    num_layers - 1        # Final layer (Q4)
]
print(f"Extracting from {len(LAYERS)} layers: {LAYERS} (out of {num_layers} total)")

extractor = HiddenStateExtractor(model, tokenizer)
hidden_states = extractor.extract(
    texts=prompts,
    layers=LAYERS,
    batch_size=8,
    show_progress=True,
)

# Shape: (num_examples, num_layers, hidden_dim)
# Flatten to (num_examples, num_layers * hidden_dim) for input to probes
# This gives probes access to multi-scale representations while keeping 2D input format
print(f"Raw hidden states shape: {hidden_states.shape}")
X = hidden_states.reshape(hidden_states.shape[0], -1)
y = correctness

print(f"Flattened hidden states shape: {X.shape}")
print(f"Labels shape: {y.shape}")
print(f"Input dimension increased from {loader.config.hidden_dim} to {X.shape[1]} (4 layers)")

## 5. Train/Val/Test Split

In [ ]:
from sklearn.model_selection import train_test_split

# 60% train, 20% val, 20% test
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.4, random_state=42, stratify=y)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42, stratify=y_temp)

print(f"Train: {len(X_train)} (acc: {y_train.mean():.1%})")
print(f"Val:   {len(X_val)} (acc: {y_val.mean():.1%})")
print(f"Test:  {len(X_test)} (acc: {y_test.mean():.1%})")

## 6. Define Architectures

In [ ]:
import sys
sys.modules.pop("src.probes", None)
sys.modules.pop("src.probes.architectures", None)

In [ ]:
import importlib
import src.probes
importlib.reload(src.probes)

import src.probes.architectures
importlib.reload(src.probes.architectures)

In [ ]:
from src.probes import (
    CalibratedProbe,
    build_default_network,
    build_attention_network,
    build_residual_network,
    build_bottleneck_network,
    build_multihead_network,
    build_gated_network,
    build_sparse_network,
    build_heteroscedastic_network,
    build_bilinear_network,
    build_contrastive_network,
    build_hierarchical_network,
)
from src.probes.architectures import build_hierarchical_network #unicorn
import torch.nn.functional as F #fix

INPUT_DIM = X.shape[1]  # 4096 for Mistral

# FIXED
# Convert training data to torch
X_train_t = torch.tensor(X_train, dtype=torch.float32)
y_train_t = torch.tensor(y_train, dtype=torch.float32)

# Separate correct and incorrect examples
correct_vecs = X_train_t[y_train_t == 1]    # (num_correct, 4096)
incorrect_vecs = X_train_t[y_train_t == 0]  # (num_incorrect, 4096)

# Compute direction of errors vs correct predictions
spurious_direction = incorrect_vecs.mean(0) - correct_vecs.mean(0)

# Normalize safest for contrastive penalty
spurious_direction = F.normalize(spurious_direction, dim=0)

# Final shape: (1, INPUT_DIM)
spurious_directions = spurious_direction.unsqueeze(0)


# Define all architectures to test
ARCHITECTURES = {
    "Linear": lambda: build_default_network(INPUT_DIM, hidden_dim=None),
    "Default MLP": lambda: build_default_network(INPUT_DIM, hidden_dim=256),
    "Attention": lambda: build_attention_network(INPUT_DIM, num_chunks=16, num_heads=4),
    "Residual": lambda: build_residual_network(INPUT_DIM, hidden_dim=256, num_blocks=3),
    "Bottleneck": lambda: build_bottleneck_network(INPUT_DIM, bottleneck_dim=64),
    "MultiHead": lambda: build_multihead_network(INPUT_DIM, num_heads=4, head_dim=128),
    "Gated": lambda: build_gated_network(INPUT_DIM, hidden_dim=256, num_layers=2),
    "Sparse (k=256)": lambda: build_sparse_network(INPUT_DIM, k=256, hidden_dim=128),
    "Heteroscedastic": lambda: build_heteroscedastic_network(INPUT_DIM, hidden_dim=256),
    "Bilinear": lambda: build_bilinear_network(INPUT_DIM, num_factors=32, hidden_dim=128),
    "Contrastive": lambda: build_contrastive_network(INPUT_DIM, spurious_directions=spurious_directions, dropout=0.1), # FIXED
    "Hierarchical": lambda: build_hierarchical_network(INPUT_DIM, num_chunks=16, hidden_dim=256, dropout=0.1)
}

print(f"Testing {len(ARCHITECTURES)} architectures")

## 7. Train All Architectures

In [ ]:
from sklearn.metrics import roc_auc_score, brier_score_loss

def compute_ece(confidences, labels, num_bins=10):
    """Compute Expected Calibration Error."""
    bin_boundaries = np.linspace(0, 1, num_bins + 1)
    ece = 0.0

    for i in range(num_bins):
        mask = (confidences > bin_boundaries[i]) & (confidences <= bin_boundaries[i + 1])
        if mask.sum() > 0:
            bin_conf = confidences[mask].mean()
            bin_acc = labels[mask].mean()
            ece += mask.sum() * abs(bin_conf - bin_acc)

    return ece / len(confidences)

# Store results
results = {}

# Training settings - NO early stopping, use scheduler for better convergence
NUM_EPOCHS = 200
PATIENCE = None  # Disable early stopping - train for full epochs

for name, build_fn in ARCHITECTURES.items():
    print(f"\n{'='*50}")
    print(f"Training: {name}")
    print('='*50)

    # Build network and probe
    network = build_fn()
    probe = CalibratedProbe(network=network)

    # Count parameters
    num_params = sum(p.numel() for p in probe.parameters())
    print(f"Parameters: {num_params:,}")

    # Train with NO early stopping
    history = probe.fit(
        X_train, y_train,
        X_val, y_val,
        batch_size=32,
        num_epochs=NUM_EPOCHS,
        patience=PATIENCE,  # None = no early stopping
        use_scheduler=True,  # Cosine annealing LR
        verbose=True,
    )

    # Evaluate on test set
    confidences = probe.predict(X_test)
    predictions = (confidences > 0.5).astype(int)

    # Compute metrics
    accuracy = (predictions == y_test).mean()
    auroc = roc_auc_score(y_test, confidences)
    brier = brier_score_loss(y_test, confidences)
    ece = compute_ece(confidences, y_test)

    results[name] = {
        "accuracy": accuracy,
        "auroc": auroc,
        "brier": brier,
        "ece": ece,
        "num_params": num_params,
        "best_epoch": history["best_epoch"],
        "confidences": confidences,
    }

    print(f"\nTest Results:")
    print(f"  Accuracy: {accuracy:.3f}")
    print(f"  AUROC:    {auroc:.3f}")
    print(f"  Brier:    {brier:.4f}")
    print(f"  ECE:      {ece:.4f}")

## 8. Results Comparison

In [ ]:
import pandas as pd

# Create results DataFrame
df = pd.DataFrame({
    name: {
        "Accuracy": f"{r['accuracy']:.3f}",
        "AUROC": f"{r['auroc']:.3f}",
        "Brier Score": f"{r['brier']:.4f}",
        "ECE": f"{r['ece']:.4f}",
        "Parameters": f"{r['num_params']:,}",
    }
    for name, r in results.items()
}).T

print("\n" + "="*70)
print("ARCHITECTURE COMPARISON")
print("="*70)
print(df.to_string())

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns

# Set style
plt.style.use('seaborn-v0_8-whitegrid')
fig, axes = plt.subplots(2, 2, figsize=(14, 10))

names = list(results.keys())
colors = sns.color_palette("husl", len(names))

# 1. AUROC comparison
ax1 = axes[0, 0]
aurocs = [results[n]["auroc"] for n in names]
bars = ax1.barh(names, aurocs, color=colors)
ax1.set_xlabel("AUROC (higher is better)")
ax1.set_title("Discrimination: AUROC")
ax1.set_xlim(0.5, 1.0)
for bar, val in zip(bars, aurocs):
    ax1.text(val + 0.01, bar.get_y() + bar.get_height()/2, f"{val:.3f}", va='center')

# 2. Brier Score comparison
ax2 = axes[0, 1]
briers = [results[n]["brier"] for n in names]
bars = ax2.barh(names, briers, color=colors)
ax2.set_xlabel("Brier Score (lower is better)")
ax2.set_title("Calibration: Brier Score")
for bar, val in zip(bars, briers):
    ax2.text(val + 0.005, bar.get_y() + bar.get_height()/2, f"{val:.4f}", va='center')

# 3. ECE comparison
ax3 = axes[1, 0]
eces = [results[n]["ece"] for n in names]
bars = ax3.barh(names, eces, color=colors)
ax3.set_xlabel("ECE (lower is better)")
ax3.set_title("Calibration: Expected Calibration Error")
for bar, val in zip(bars, eces):
    ax3.text(val + 0.005, bar.get_y() + bar.get_height()/2, f"{val:.4f}", va='center')

# 4. Parameters vs AUROC (efficiency)
ax4 = axes[1, 1]
params = [results[n]["num_params"] for n in names]
for i, name in enumerate(names):
    ax4.scatter(params[i], aurocs[i], s=150, c=[colors[i]], label=name, edgecolors='black')
ax4.set_xlabel("Number of Parameters")
ax4.set_ylabel("AUROC")
ax4.set_title("Efficiency: Parameters vs Performance")
ax4.set_xscale('log')
ax4.legend(bbox_to_anchor=(1.05, 1), loc='upper left', fontsize=8)

plt.tight_layout()
plt.savefig("architecture_comparison.png", dpi=150, bbox_inches='tight')
plt.show()

print("\nSaved: architecture_comparison.png")

## 9. Reliability Diagrams

In [ ]:
def plot_reliability_diagram(confidences, labels, title, ax, num_bins=10):
    """Plot reliability diagram."""
    bin_boundaries = np.linspace(0, 1, num_bins + 1)
    bin_centers = (bin_boundaries[:-1] + bin_boundaries[1:]) / 2

    bin_accs = []
    bin_confs = []
    bin_counts = []

    for i in range(num_bins):
        mask = (confidences > bin_boundaries[i]) & (confidences <= bin_boundaries[i + 1])
        if mask.sum() > 0:
            bin_accs.append(labels[mask].mean())
            bin_confs.append(confidences[mask].mean())
            bin_counts.append(mask.sum())
        else:
            bin_accs.append(np.nan)
            bin_confs.append(np.nan)
            bin_counts.append(0)

    # Plot
    ax.bar(bin_centers, bin_accs, width=0.08, alpha=0.7, label='Accuracy')
    ax.plot([0, 1], [0, 1], 'k--', label='Perfect calibration')
    ax.set_xlabel('Confidence')
    ax.set_ylabel('Accuracy')
    ax.set_title(title)
    ax.set_xlim(0, 1)
    ax.set_ylim(0, 1)
    ax.legend(loc='lower right')

# Plot reliability diagrams for all architectures
fig, axes = plt.subplots(4, 3, figsize=(15, 16))
axes = axes.flatten()

for i, (name, r) in enumerate(results.items()):
    if i < len(axes):
        plot_reliability_diagram(
            r["confidences"], y_test,
            f"{name}\nECE={r['ece']:.4f}",
            axes[i]
        )

# Hide unused subplots
for i in range(len(results), len(axes)):
    axes[i].axis('off')

plt.tight_layout()
plt.savefig("reliability_diagrams.png", dpi=150, bbox_inches='tight')
plt.show()

print("\nSaved: reliability_diagrams.png")

## 10. Summary & Recommendations

In [ ]:
# Find best architectures for each metric
best_auroc = max(results.items(), key=lambda x: x[1]["auroc"])
best_brier = min(results.items(), key=lambda x: x[1]["brier"])
best_ece = min(results.items(), key=lambda x: x[1]["ece"])
best_efficiency = max(results.items(), key=lambda x: x[1]["auroc"] / np.log10(x[1]["num_params"]))

print("="*60)
print("RECOMMENDATIONS")
print("="*60)
print(f"\nBest Discrimination (AUROC): {best_auroc[0]}")
print(f"  AUROC = {best_auroc[1]['auroc']:.4f}")

print(f"\nBest Calibration (Brier): {best_brier[0]}")
print(f"  Brier = {best_brier[1]['brier']:.4f}")

print(f"\nBest Calibration (ECE): {best_ece[0]}")
print(f"  ECE = {best_ece[1]['ece']:.4f}")

print(f"\nMost Efficient (AUROC/log(params)): {best_efficiency[0]}")
print(f"  AUROC = {best_efficiency[1]['auroc']:.4f}, Params = {best_efficiency[1]['num_params']:,}")

print("\n" + "="*60)
print("NOTES")
print("="*60)
print("""
- Lower Brier/ECE = better calibration (confidence matches accuracy)
- Higher AUROC = better discrimination (separating correct/incorrect)
- SparseProbe is most interpretable (shows which dimensions matter)
- HeteroscedasticProbe handles varying example difficulty
- For production: prioritize calibration (Brier/ECE)
- For research: prioritize AUROC and interpretability
""")

## 11. Sparse Probe Analysis (Interpretability)

In [ ]:
# If SparseProbe performed well, analyze which dimensions it selected
from src.probes.architectures import TopKSparseNetwork

# Retrain sparse probe to access its learned importance weights
sparse_network = build_sparse_network(INPUT_DIM, k=256, hidden_dim=128)
sparse_probe = CalibratedProbe(network=sparse_network)
sparse_probe.fit(X_train, y_train, X_val, y_val, num_epochs=200, patience=None, verbose=False)

# Get importance scores using the new API
importance = sparse_probe.network.get_importance_scores().cpu().numpy()

# Find top dimensions
top_k = 20
top_indices = np.argsort(importance)[-top_k:][::-1]
top_scores = importance[top_indices]

print(f"Top {top_k} most important dimensions for confidence:")
print("="*40)
for idx, score in zip(top_indices, top_scores):
    print(f"  Dim {idx:4d}: importance = {score:.4f}")

# Plot importance distribution
plt.figure(figsize=(12, 4))

plt.subplot(1, 2, 1)
plt.bar(range(top_k), top_scores)
plt.xlabel("Rank")
plt.ylabel("Importance Score")
plt.title(f"Top {top_k} Dimensions")
plt.xticks(range(top_k), top_indices, rotation=45)

plt.subplot(1, 2, 2)
plt.hist(importance, bins=50, edgecolor='black')
plt.xlabel("Importance Score")
plt.ylabel("Count")
plt.title("Importance Distribution (All Dimensions)")
# Show threshold for top-256 dimensions
sorted_importance = np.sort(importance)[::-1]
if len(sorted_importance) > 256:
    threshold = sorted_importance[255]
    plt.axvline(threshold, color='r', linestyle='--', label=f'Top 256 threshold ({threshold:.3f})')
    plt.legend()

plt.tight_layout()
plt.savefig("sparse_probe_importance.png", dpi=150)
plt.show()

print("\nSaved: sparse_probe_importance.png")